# Problem Set 1: The Adventures of the Dark Genomes

The objective of this pset is to test two hypotheses: 1) whether high GC composition can artificially inflate our calculation of protein-encoding long ORFs in phage, and 2) whether TAG/TGA recoding might account for abnormally low long-ORF coverage statistics for certain phage. First, I import the relevant modules into my workbook:

In [19]:
import numpy as np                    
import matplotlib.pyplot as plt
import watermark

%matplotlib inline

and now I begin my first task, which is to create a function in Python that calculates the long-ORF coverage statistic from a phage genome sequence.

## Task 1: Calculating the Long ORF Fraction

Here, I am trying to write a function that calculates the long ORF coverage fraction when given a DNA sequence, a minimum ORF length, and a set of known stop codons as inputs. I start by defining a desired set of stop codons, as well as a minimum long-ORF threshold length (in terms of amino acid count), and storing them into respective variables as such:

In [2]:
stops_standard = ['TAA','TAG','TGA'] # The standard set of stop codons we will be using
min_length = 200                     # Minimum long ORF length we set here as 200aa (or 600bp)

Since Lestrade used a minimum length of 200aa as his threshold for his long-ORF analysis, I adopt it as my minimum as well. For future purposes, I decided I may as well also create sets of stop codons for TAG- and TGA-recoded phage: 

In [3]:
stops_TAG = ['TAA','TGA']            # TAG-recoded 
stops_TGA = ['TAA','TAG']            # TGA-recoded 

Next, I generate a random test sequence of nucleotides, which I call 'test_seq': 

In [4]:
test_seq = 'ATCGATCGATCGATCGATCGATCG'

then create a function 'revcomp()' that generates the reverse complement of a given DNA sequence. Below, I feed the test sequence into the function to ensure it works as intended.

In [5]:
# Create function that generates reverse complement of a given DNA sequence
def revcomp(seq):           
    reversed_seq = seq[::-1]                                            # Reverse DNA sequence 
    revcomp_seq = reversed_seq.translate(str.maketrans('ACGT', 'TGCA')) # Create its complement w/ translation table
    return revcomp_seq
revcomp(test_seq)

'CGATCGATCGATCGATCGATCGAT'

Now that I have both the original and the complementary strand of the genome, I can create a dictionary containing all six possible reading frames. First, I create a list of tuples, and return a dictionary out of those tuples (with "frame#" as the key and the sequence as the corresponding value):

In [6]:
# Create function that generates dictionary with each of the six reading frames stored in a 'frame#' key
# Three coding frames each with their own start position shifted one nucleotide apart
# For both the original sequence (#1-3) and its reverse complement (#4-6)

def frames(seq):
    tuple_list = [("frame1", seq),("frame2", seq[1:]),("frame3", seq[2:]),
                  ("frame4", revcomp(seq)),("frame5", revcomp(seq)[1:]),("frame6", revcomp(seq)[2:])]
    return dict(tuple_list)

print(frames(test_seq))

{'frame1': 'ATCGATCGATCGATCGATCGATCG', 'frame2': 'TCGATCGATCGATCGATCGATCG', 'frame3': 'CGATCGATCGATCGATCGATCG', 'frame4': 'CGATCGATCGATCGATCGATCGAT', 'frame5': 'GATCGATCGATCGATCGATCGAT', 'frame6': 'ATCGATCGATCGATCGATCGAT'}


Once again, I've fed this function my test sequence to ensure it works as I intended. 

And finally, to obtain the long ORF coverage fraction for a given genome sequence, I nest everything into for loops to create one large function. The 'longORFfrac' function takes in a genome sequence 'genome_seq' as a string, a list of stop codons 'stops' as a list of strings, and a minimum ORF length 'min_length' as an integer. I ensure that all six reading frames of the input genome are accounted for by passing the genome through the 'frames' function I made previously and iterating each frame through the reading process. Next, I read each frame in terms of triplets, and measure the total length of triplet runs that are >= 200 amino acids long and are uninterrupted by any of the stop codons we defined earlier. (Essentially, I am measuring >= 200aa stretches of triplets bookended by stop codons, and adding the lengths of these stretches together.) Finally, I divide the total sum of long ORF lengths by the total genome length to obtain our long ORF coverage fraction.

The function has been made below, with comments explaining each line of code:

In [7]:
def longORFfrac(genome_seq, stops, min_length):
    ORF_total = 0                                    # Create object to add lengths of long ORFs (in bp)
    reading_frames = frames(genome_seq)              # Create dictionary of frames for input genome sequence
    for key in reading_frames:                       # Iterate through all six possible reading frames
        frame_seq = reading_frames[key]              # Access the sequence in a given frame
        triplets = [frame_seq[i:i+3] for i in range(0, len(frame_seq), 3)] # Create triplet list from sequence
        indices = [i for i, triplet in enumerate(triplets) if triplet in stops] # Index each stop codon position 
        for i in range(1, len(indices)):             # Access every position of a stop codon in our list of triplets 
            distance = indices[i] - indices[i-1] - 1 # Subtract 1 to exclude the triplet itself
            if distance >= min_length:               # Ensure ORF meets the threshold minimum length
                ORF_length = distance*3              # Length of the long ORF in nucleotides
                ORF_total = ORF_total + ORF_length   # Update our long ORF count 
    coverage_frac = ORF_total/len(genome_seq)        # Divide sum of long ORF lengths by entire genome length
    return coverage_frac

Now, let's move onto Task 2, where I'll be implementing 'longORFfrac' to conduct a negative control experiment to determine whether GC composition in a given genome may be affecting our long ORF coverage statistic. 

## Task 2: Creating the Negative Control — Generating a Random DNA Sequence

Here we are generating random DNA sequences of specified GC compositions to act as our negative control (against which we can compare our actual phage to infer the role of GC composition in calculating long ORF coverage). So first, I define a function 'neg_control' that takes in GC composition and genome size as inputs:

In [8]:
rng = np.random.default_rng() # Leaving seed empty 
# Define function 'neg_control' to create random sequence 
def neg_control(GC, genome_size):   # 'GC' for GC content, 'genome_size' for genome length
    p_GC = GC                       # GC composition (number between 0 and 1) 
    p_AT = 1 - GC                   # AT composition (constraint so probabilities sum to 1)
    # Create random sequence of S (G or C) and W (A or T) with GC content specified
    seq = np.random.choice(list('SW'), size = genome_size, p=[p_GC, p_AT]) 
    for i in range(len(seq)):       # Iterate process by genome-length # of times
        if seq[i] == 'S':           # for every instance of 'S' in the sequence
            if rng.random() < 0.5:  # Generate a random number between 0 and 1
                # Sample evenly between 'G' and 'C' to replace 'S'
                seq[i] = 'G'
            else:
                seq[i] = 'C'
        else: # Remainder of cases, i.e. the Ws in the sequence
            if rng.random() < 0.5:
                # Sample evenly between 'A' and 'T' to replace 'W'
                seq[i] = 'A'
            else:
               seq[i] = 'T'
    array_str = seq.astype(str)     # Convert numpy ndarray object type to string
    result = ''.join([char for char in array_str if char.isalpha()]) 
    return(result)  

So for example, I can create a random DNA sequence of length 200bp with a GC content of 80%:

In [9]:
neg_control(0.8, 200)

'ATCGGGGTGGCGCCAGGGCGGCGCCGGCGGGCGGCTCAGTGGCGCCCGCGGGCGACCCCTCCCCGGAGACTATTCGCGGGCGCCCAAGCACGCCGGGCCCCGCGCAGGTCGCCCTACGCGGCGCGGGCGGTCCGGCGGGGGCCCGCCGGACCCCGCGCCGCGGCGGACCGCCGCAAGCCATCGTGGCCACACCGCCGGAT'

Now, to run our negative control experiment, I create two vectors, one storing incrementally increasing GC compositions (as probability values) and the other storing genome lengths.

In [20]:
gc = [0.2, 0.32, 0.40, 0.48, 0.56, 0.64, 0.72, 0.8, 1]
lengths = [50000, 100000, 150000, 200000]

(I'm skipping ahead a bit here, but the reason why I chose these specific genome lengths is because I wanted these lengths to approximate the same orders of magnitude as the genome lengths for the phage that Moriarty gave us, rather than just make inferences based off one phage genome size (ex. T4). Below, I use a function 'unFASTA' (which I explain later in Task 4) that obtains the phage genome files from Moriarty and sorts their lengths, and we see that the smallest genome in Moriarty's set is ~90000bp while the largest is ~175000bp. Therefore, for my negative control experiment, I use four genome lengths that cover the range of genome sizes spanning Moriarty's set. For the vector of GC content values, I chose them based off the strip plot from Wiggins' reanalysis.)

In [21]:
# Here we obtain Moriarty's phage genome FASTA files using the function 'unFASTA' which I introduce later:
genomes = ['arugula.fa','basil.fa','chickpea.fa','gooseberry.fa','huckleberry.fa',
           'juniper.fa','lentil.fa','quince.fa','sage.fa','tangerine.fa']

# For more info on this function see Task 4
def unFASTA(file):
    with open(file, 'r') as file:              # Open FASTA file in cell as a readable object
        sequence = file.read()                 # Read file's contents (both header and DNA sequence) as a string
        sequence = sequence.replace('\n','')   # Delete line breaks in string 
    x = len(file.name)                         # Obtain length of FASTA file name
    return(sequence[x-2:])                     # Delete header by shifting two positions

# And now we obtain the sorted genome lengths 
sizes = []
for genome in genomes: 
    sequence = unFASTA(genome)
    sizes.append(len(sequence))
print(sorted(sizes))

[92533, 93375, 95597, 96106, 97130, 97526, 97874, 102591, 174484, 175988]


(The sorted sizes of the phage genomes that Moriarty gave us are printed above.)

Next, I create a function that iterates through different possible genome sizes and GC contents to create random synthetic DNA sequences (using the 'neg_control' and 'longORFfrac' functions made earlier), and obtains the long ORF coverage fraction from these sequences: 

In [22]:
# Create simulation function to perform negative control experiment 
def simulation(GC, genome_size, stops, min_length):
    # Header indicating print order of simulated data; left-indented
    print("{:<20} {:<20} {:<20}".format("Genome size", "GC composition", "Long ORF coverage"))
    rows = []
    for j in range(len(genome_size)):                           # Iterate through different genome sizes
        for i in range(len(GC)):                                # Iterate through different GC contents
            synthetic = neg_control(GC[i], genome_size[j])      # Generate the random DNA sequence
            result = longORFfrac(synthetic, stops, min_length)  # Perform long ORF coverage fraction calc
            rows.append([f"{genome_size[j]} bp", f"{GC[i]}", f"{result}"])  # Add new data as new list row
    for row in rows:                                            # Iterating through every data row
        print(f"{row[0]:<20} {row[1]:<20} {row[2]:<20}")        # Print results in table format; left-indented

Finally, I feed my GC content and genome length vectors into my function to conduct my negative control experiment to see whether GC composition affects our long ORF coverage fraction calculations. 

In [23]:
simulation(gc, lengths, stops_standard, min_length)

Genome size          GC composition       Long ORF coverage   
50000 bp             0.2                  0.0                 
50000 bp             0.32                 0.0                 
50000 bp             0.4                  0.0                 
50000 bp             0.48                 0.0                 
50000 bp             0.56                 0.01602             
50000 bp             0.64                 0.20964             
50000 bp             0.72                 0.96312             
50000 bp             0.8                  2.86314             
50000 bp             1                    0.0                 
100000 bp            0.2                  0.0                 
100000 bp            0.32                 0.0                 
100000 bp            0.4                  0.0                 
100000 bp            0.48                 0.00678             
100000 bp            0.56                 0.02586             
100000 bp            0.64                 0.2235       

By randomly constructing sequences of four different sizes and running these simulations, we can see that our long ORF coverage calculations increase with GC content when genome size is held constant, and this pattern holds true for all different genome sizes. Most notably, when GC content is >= 64%, our simulation consistently outputs a long ORF coverage fraction > 0.1 (just a pattern I observed from multiple runs, not really a robust statistical cutoff). In summary, higher GC composition is likely artificially inflating our long ORF coverage statistic, especially for phage with GC composition >60%. For sequences with 72% GC, the long-ORF coverage statistic is consistently close to 1, which is alarmingly high given that these genetic sequences are synthesized randomly (i.e. without any intentional inclusion of 200aa-long protein-encoding ORFs). Thus, since there are many "spurious" long-ORFs (that is, long-ORFs that occurred completely by chance, and are non-protein-encoding stretches of triplets lacking stop codons) in our artificial phage, our simulation suggests that spurious long-ORFs in phage with GC composition > 60% are likely inflating our coverage fraction calculations for those phage. 

In summary, this negative control experiment helps us to visualize how GC composition could be affecting our probability of seeing long ORFs even when they aren't true protein-encoding regions, and therefore aids us in defending our first hypothesis from Moriarty's attacks. 

## Task 3: Obtaining Moriarty's 10 Phage Genomes via 1st Method (Untar via Terminal)

I used shells commands in my terminal to unzip and untar the .tar.gz file and obtain the 10 phage genomes from Moriarty.

## Task 4: Getting DNA Sequences from FASTA Format

Since the DNA sequences we get from Moriarty are in FASTA format, we have to read the FASTA files into our cell, parse their content, and return the DNA sequence. I do this by creating the function 'unFASTA', which performs the previously mentioned steps:

In [14]:
def unFASTA(file):
    with open(file, 'r') as file:              # Open FASTA file in cell as a readable object
        sequence = file.read()                 # Read file's contents (both header and DNA sequence) as a string
        sequence = sequence.replace('\n','')   # Delete line breaks in string 
    x = len(file.name)                         # Obtain length of FASTA file name
    return(sequence[x-2:])                     # Delete header by shifting two positions

Since our FASTA files include a header (in the format '>[filename]) followed by the actual DNA sequence peppered with line breaks, I remove the line breaks first, then I remove the header by taking the FASTA file name's length into account. For example, below I've printed the first 20 characters of the genome file 'arugula.fa':

In [15]:
with open('arugula.fa', 'r') as file:           
    sequence = file.read()                 
print(sequence[:20])

>arugula
TTATTACAGAC


Since the FASTA file name is formatted "[filename].fa", while the header text in the FASTA file is formatted as ">[filename]", the two differ in length by 2 characters (the FASTA file name is longer). Using this knowledge, 'unFASTA' obtains the DNA sequence by reading in the text from the FASTA file, deleting line breaks, then shifting to the start point of the DNA sequence by referencing the FASTA file name and going back two characters.

## Task 5: Putting It All Together

Now that I've created a function that can calculate the long ORF fraction for a genome from a given list of stop codons, as well as a function that can read in and obtain the nucleotide sequence from a FASTA file, I can combine the two into a larger function below, which I call 'pipeline':

In [16]:
# Moriarty's phage genome files in FASTA format we want to pass through our pipeline
genomes = ['arugula.fa','basil.fa','chickpea.fa','gooseberry.fa','huckleberry.fa',
           'juniper.fa','lentil.fa','quince.fa','sage.fa','tangerine.fa']

# Stop codon varieties we're accounting for
stops = [stops_standard, stops_TAG, stops_TGA]

# Putting it all together in 'pipeline' function
def pipeline(genomes, stops, min_length):
    # Header indicating print order of our calculation data "table"; left-indented
    print("{:<15} {:<15} {:<15} {:<15} {:<15} {:<15}".format("Phage name", "Standard ORF", "TAG recoded", "TGA recoded", "TAG:standard", "TGA:standard"))
    for genome in genomes:                        # Iterate process through every phage genome
        genome_seq = unFASTA(genome)              # Read sequence from FASTA file
        genome = genome[:-3]                      # Delete ".fa" from file name
        fractions = []                            # List we're collecting our calculations into
        for i in range(len(stops)):               # Iterate through every stop codon recoding paradigm
            new_fraction = longORFfrac(genome_seq, stops[i], min_length) # Calculate ORF coverage frac
            fractions.append(float("{:.6f}".format(new_fraction)))  # Add new rounded calculation to list
        col4 = fractions[1]/fractions[0]          # TAG:standard ratio
        col4 = f"{col4:.6f}"                      # Rounded ratio
        col5 = fractions[2]/fractions[0]          # TGA:standard ratio
        col5 = f"{col5:.6f}"                      # Rounded ratio
        # Printing each row of our "table" of calculations; left-indented
        print(f"{genome:<15} {fractions[0]:<15} {fractions[1]:<15} {fractions[2]:<15} {col4:<15} {col5:<15}")

What 'pipeline' does here is it takes any collection of genome sequence files in FASTA format, and returns the long ORF coverage fraction given whatever genetic code paradigm we want (i.e. standard, TAG-recoded, TGA-recoded) and a minimum length we specify for our long ORF. Finally, I've sent all of Moriarty's phage genomes through my pipeline to obtain the long ORF coverage statistic calculations below:

In [17]:
pipeline(genomes, stops, min_length)

Phage name      Standard ORF    TAG recoded     TGA recoded     TAG:standard    TGA:standard   
arugula         0.367512        0.390173        0.731551        1.061661        1.990550       
basil           0.771302        0.845559        0.848358        1.096275        1.099904       
chickpea        0.842192        0.882957        0.918889        1.048403        1.091068       
gooseberry      0.288973        0.77615         0.386584        2.685891        1.337786       
huckleberry     0.797651        0.860223        0.838339        1.078445        1.051010       
juniper         0.285144        0.733337        0.346731        2.571813        1.215986       
lentil          0.369196        0.384435        0.739278        1.041276        2.002400       
quince          0.793155        0.873286        0.883025        1.101028        1.113307       
sage            0.759197        0.844112        0.83653         1.111848        1.101862       
tangerine       0.690551        0.734935

From our output, we can see that the TAG-recoded:standard coverage ratios for the 'gooseberry' and 'juniper' phage (approx. 2.5-2.7) and the TGA-recoded:standard coverage ratios for the 'arugula' and 'lentil' phage (~2 for both) are remarkably high, while all other ratios for all phage hold close to 1 (1.00-1.35). Therefore, we can identify the two TAG-recoded phage as 'gooseberry' and 'juniper', and the two TGA-recoded phage as 'arugula' and 'lentil', with the remaining six phage using the standard code. 

We can infer the above because we know all of the phage we got from Moriarty are AT-rich, so we can expect a greater proportion of true positives (i.e. actual protein-encoding sequences) in our detected long-ORFs from these phage (this is the opposite of GC-rich phage, which as discussed before are more likely to include spurious long ORFs in their coverage statistic). Therefore, we can expect dramatic differences between recoded:standard coverage ratios for the recoded phage, since incorrectly using the standard code to read these phage genomes will induce a significant number of stops in true coding regions, and distinctly shrink the number of long ORFs we detect from them.

Thus, our data would suggest that Moriarty is wrong, and that he owes us a bag of donuts. First, we demonstrated how high GC content can inflate our long ORF coverage statistic by inducing false positives (i.e. spurious non-coding long ORFs we end up detecting in a genome sequence). And just now, we were are able to take into account the possibility of TAG/TGA recoding in our long-ORF coverage analysis, and doing so enables us to identify which two genomes are TAG-recoded (gooseberry and juniper) and which two are TGA-recoded (arugula and lentil). 


In [18]:
%load_ext watermark
%watermark -v -m -p numpy,matplotlib,seaborn,pandas,jupyterlab

Python implementation: CPython
Python version       : 3.12.5
IPython version      : 8.27.0

numpy     : 2.1.1
matplotlib: 3.9.2
seaborn   : 0.13.2
pandas    : 2.2.2
jupyterlab: 4.2.5

Compiler    : Clang 16.0.6 
OS          : Darwin
Release     : 22.6.0
Machine     : arm64
Processor   : arm
CPU cores   : 12
Architecture: 64bit

